# AtmoML Hyperparameter Tuning

In [1]:
import os
import random
import pathlib
import logging
import keras
import keras_tuner
import tensorflow as tf
import time
from collections import defaultdict

from usl_models.atmo_ml.model import AtmoModel
from usl_models.atmo_ml import dataset, visualizer, vars

# === GPU Setup ===
for gpu in tf.config.list_physical_devices('GPU'):
    tf.config.experimental.set_memory_growth(gpu, True)

# === Logging and Reproducibility ===
logging.getLogger().setLevel(logging.WARNING)
keras.utils.set_random_seed(812)
visualizer.init_plt()

# === Constants ===
batch_size = 4
timestamp = time.strftime("%Y%m%d-%H%M%S")
filecache_dir = pathlib.Path("/home/shared/climateiq/filecache")

# === Simulation folders ===
sim_folders = [
    "NYC_Heat_Test/NYC_summer_2000_01p",
    "NYC_Heat_Test/NYC_summer_2010_99p",
    "NYC_Heat_Test/NYC_summer_2015_50p",
    "NYC_Heat_Test/NYC_summer_2017_25p",
    "NYC_Heat_Test/NYC_summer_2018_75p",
    "PHX_Heat_Test/PHX_summer_2008_25p",
    "PHX_Heat_Test/PHX_summer_2009_50p",
    "PHX_Heat_Test/PHX_summer_2011_99p",
    "PHX_Heat_Test/PHX_summer_2015_75p",
    "PHX_Heat_Test/PHX_summer_2020_01p",
    "CPN_Heat/CPN_summer_2000_01p",
    "CPN_Heat/CPN_summer_2005_25p",
    "CPN_Heat/CPN_summer_2007_50p",
    "CPN_Heat/CPN_summer_2014_75p",
    "CPN_Heat/CPN_summer_2018_99p"
]

# === Helper: Extract 30 valid days with all 4 time steps ===
def extract_valid_dates(region_prefix, max_samples=30):
    daily_files = defaultdict(set)
    for folder in sim_folders:
        if folder.startswith(region_prefix):
            spatio_dir = filecache_dir / folder / "spatiotemporal"
            if not spatio_dir.exists():
                continue
            for fname in os.listdir(spatio_dir):
                if fname.startswith("met_em.d03.") and fname.endswith(".npz"):
                    try:
                        time_str = fname.split(".")[2]  # '2000-05-24_06:00:00'
                        date_str, hour_str = time_str.split("_")
                        hour = hour_str.split(":")[0]  # '06'
                        daily_files[(folder, date_str)].add(hour)
                    except Exception as e:
                        print(f"⚠️ Failed to parse {fname}: {e}")
    valid_keys = [
        (folder, date)
        for (folder, date), hours in daily_files.items()
        if {"00", "06", "12", "18"}.issubset(hours)
    ]
    random.shuffle(valid_keys)
    return valid_keys[:max_samples]

# === Collect keys ===
example_keys = (
    extract_valid_dates("NYC_Heat_Test", 30) +
    extract_valid_dates("PHX_Heat_Test", 30) +
    extract_valid_dates("CPN_Heat", 30)
)

# === Print diagnostics ===
print(f"✅ Loaded {len(example_keys)} example keys")
print("🔹 First 5:", example_keys[:5])

city_counts = defaultdict(int)
for sim, _ in example_keys:
    city = sim.split("_")[0]  # e.g., 'NYC'
    city_counts[city] += 1
print("📊 Region breakdown:", dict(city_counts))

# === Dataset loading ===
ds_config = dataset.Config(output_timesteps=2)

train_ds = dataset.load_dataset_cached(
    filecache_dir,
    example_keys=example_keys,
    config=ds_config,
).batch(batch_size=batch_size)

val_ds = dataset.load_dataset_cached(
    filecache_dir,
    example_keys=example_keys,
    config=ds_config,
    shuffle=False,
).batch(batch_size=batch_size)

# === GPU strategy ===
# strategy = tf.distribute.MirroredStrategy()
# print("✅ Number of devices:", strategy.num_replicas_in_sync)


2025-05-31 02:47:53.228197: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-05-31 02:47:53.296159: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-05-31 02:47:53.296196: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-05-31 02:47:53.298366: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-05-31 02:47:53.310487: I tensorflow/core/platform/cpu_feature_guar

✅ Loaded 90 example keys
🔹 First 5: [('NYC_Heat_Test/NYC_summer_2017_25p', '2017-07-26'), ('NYC_Heat_Test/NYC_summer_2017_25p', '2017-06-20'), ('NYC_Heat_Test/NYC_summer_2000_01p', '2000-06-26'), ('NYC_Heat_Test/NYC_summer_2010_99p', '2010-07-24'), ('NYC_Heat_Test/NYC_summer_2018_75p', '2018-06-30')]
📊 Region breakdown: {'NYC': 30, 'PHX': 30, 'CPN': 30}


2025-05-31 02:47:56.560022: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1929] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 38364 MB memory:  -> device: 0, name: NVIDIA A100-SXM4-40GB, pci bus id: 0000:00:04.0, compute capability: 8.0


In [2]:
for inputs, labels in train_ds.take(1):
    print("📦 Inputs:")
    for k, v in inputs.items():
        print(f"  - {k}: shape={v.shape}, dtype={v.dtype}")
    
    print("📦 Labels:")
    print(f"  - shape={labels.shape}, dtype={labels.dtype}")


📦 Inputs:
  - spatiotemporal: shape=(4, 6, 200, 200, 12), dtype=<dtype: 'float32'>
  - spatial: shape=(4, 200, 200, 22), dtype=<dtype: 'float32'>
  - lu_index: shape=(4, 200, 200), dtype=<dtype: 'int32'>
  - sim_name: shape=(4,), dtype=<dtype: 'string'>
  - date: shape=(4,), dtype=<dtype: 'string'>
📦 Labels:
  - shape=(4, 2, 200, 200, 1), dtype=<dtype: 'float32'>


In [3]:
# with strategy.scope():
tuner = keras_tuner.BayesianOptimization(
    AtmoModel.get_hypermodel(
        input_cnn_kernel_size=[1, 2, 5],
        lstm_kernel_size=[5, 3],
        spatial_activation=["relu"],
        st_activation=["relu"],
        lstm_activation=["relu"],
        output_activation=["tanh"],
    ),
    objective="val_loss",
    max_trials=5,
    project_name=f"logs/htune_project_{timestamp}",
)
tuner.search_space_summary()


Search space summary
Default search space size: 6
input_cnn_kernel_size (Choice)
{'default': 1, 'conditions': [], 'values': [1, 2, 5], 'ordered': True}
lstm_kernel_size (Choice)
{'default': 5, 'conditions': [], 'values': [5, 3], 'ordered': True}
spatial_activation (Choice)
{'default': 'relu', 'conditions': [], 'values': ['relu'], 'ordered': False}
st_activation (Choice)
{'default': 'relu', 'conditions': [], 'values': ['relu'], 'ordered': False}
lstm_activation (Choice)
{'default': 'relu', 'conditions': [], 'values': ['relu'], 'ordered': False}
output_activation (Choice)
{'default': 'tanh', 'conditions': [], 'values': ['tanh'], 'ordered': False}


In [4]:
log_dir = f"logs/htune_{timestamp}"
print(log_dir)
tb_callback = keras.callbacks.TensorBoard(log_dir=log_dir)
tuner.search(train_ds, epochs=10, validation_data=val_ds, callbacks=[tb_callback])
best_model, best_hp = tuner.get_best_models()[0], tuner.get_best_hyperparameters()[0]
best_hp.values

Trial 5 Complete [00h 03m 00s]
val_loss: 0.0018759215017780662

Best val_loss So Far: 0.0018407671013846993
Total elapsed time: 00h 10m 49s


{'input_cnn_kernel_size': 5,
 'lstm_kernel_size': 3,
 'spatial_activation': 'relu',
 'st_activation': 'relu',
 'lstm_activation': 'relu',
 'output_activation': 'tanh'}

In [ ]:
# with strategy.scope():
    # Re-create the model using the best hyperparameters
final_params = AtmoModel.Params(**best_hp.values)
model = AtmoModel(params=final_params)
tb_callback = keras.callbacks.TensorBoard(log_dir=log_dir)
model.fit(train_ds, val_ds, epochs=1000, callbacks=[tb_callback], validation_freq=1)
model.save_model(log_dir + "/model")


Epoch 1/1000


2025-05-30 20:00:21.073330: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:961] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inatmo_conv_lstm_1/conv_lstm/conv_lstm2d_1/while/body/_1/atmo_conv_lstm_1/conv_lstm/conv_lstm2d_1/while/dropout_7/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


      7/Unknown - 10s 416ms/step - loss: 0.2279 - mean_absolute_error: 0.3192 - root_mean_squared_error: 0.4774 - mean_squared_logarithmic_error: 0.0729 - nrmse: 0.8047 - ssim_metric: 0.3580 - psnr_metric: 11.2483 - mse_t2: 0.2279

     11/Unknown - 12s 451ms/step - loss: 0.1632 - mean_absolute_error: 0.2690 - root_mean_squared_error: 0.4040 - mean_squared_logarithmic_error: 0.0543 - nrmse: 0.6809 - ssim_metric: 0.3706 - psnr_metric: 12.7564 - mse_t2: 0.1632

     13/Unknown - 13s 448ms/step - loss: 0.1398 - mean_absolute_error: 0.2404 - root_mean_squared_error: 0.3739 - mean_squared_logarithmic_error: 0.0467 - nrmse: 0.6303 - ssim_metric: 0.3916 - psnr_metric: 13.9727 - mse_t2: 0.1398

...

13/20 [==================>...........] - ETA: 3s - loss: 3.0326e-04 - mean_absolute_error: 0.0132 - root_mean_squared_error: 0.0174 - mean_squared_logarithmic_error: 1.2899e-04 - nrmse: 0.0294 - ssim_metric: 0.9512 - psnr_metric: 36.1589 - mse_t2: 3.0326e-04

16/20 [=======================>......] - ETA: 1s - loss: 3.5316e-04 - mean_absolute_error: 0.0138 - root_mean_squared_error: 0.0188 - mean_squared_logarithmic_error: 1.4593e-04 - nrmse: 0.0317 - ssim_metric: 0.9490 - psnr_metric: 35.8765 - mse_t2: 3.5316e-04

18/20 [==========================>...] - ETA: 0s - loss: 3.4379e-04 - mean_absolute_error: 0.0137 - root_mean_squared_error: 0.0185 - mean_squared_logarithmic_error: 1.4267e-04 - nrmse: 0.0313 - ssim_metric: 0.9487 - psnr_metric: 35.9342 - mse_t2: 3.4379e-04

19/20 [===========================>..] - ETA: 0s - loss: 3.3542e-04 - mean_absolute_error: 0.0136 - root_mean_squared_error: 0.0183 - mean_squared_logarithmic_error: 1.3964e-04 - nrmse: 0.0309 - ssim_metric: 0.9496 - psnr_metric: 36.0241 - mse_t2: 3.3542e-04

20/20 [==============================] - ETA: 0s - loss: 3.2925e-04 - mean_absolute_error: 0.0135 - root_mean_squared_error: 0.0181 - mean_squared_logarithmic_error: 1.3765e-04 - nrmse: 0.0306 - ssim_metric: 0.9504 - psnr_metric: 36.0832 - mse_t2: 3.2925e-04

In [ ]:
# Plot results
model = AtmoModel.from_checkpoint('/home/elhajjas/climateiq-cnn-10/usl_models/notebooks/logs/htune_20250529-150138/model')
input_batch, label_batch = next(iter(train_ds))
pred_batch = model.call(input_batch)

for fig in visualizer.plot_batch(
    ds_config,
    input_batch=input_batch,
    label_batch=label_batch,
    pred_batch=pred_batch,
    st_var=vars.Spatiotemporal.TT,
    sto_var=vars.SpatiotemporalOutput.T2,
    max_examples=None,
    dynamic_colorscale=True,  # Set to True to compute from data
    unscale= True    # Revert normalization to show true values
):
    fig.show()

TypeError: Error when deserializing class 'OutputVarMeanSquaredError' using config={'name': 'mse_RH2', 'dtype': 'float32', 'sto_var': <SpatiotemporalOutput.RH2: 0>}.

Exception encountered: OutputVarMeanSquaredError.__init__() missing 1 required positional argument: 'var_index'